# `plotly` 创建图

参考：[Creating and Updating Figures | Python | Plotly](https://plotly.com/python/creating-and-updating-figures/)

```{tip}
与使用 Python 字典相比，**推荐的替代方法**是使用 Plotly Express [一次性创建整个图形](https://daobook.github.io/plotly-book/tutorial/fundamentals/03_plotly-express.html#plotly-plotly-express)，并操作生成的 `plotly.graph_objects.Figure` 对象，而不是从底层图形对象自底向上组合图。参见 [何时直接使用图对象](https://daobook.github.io/plotly-book/tutorial/fundamentals/34_graph-objects.html#plotly-when-use-graph-objects)。
```

## `plotly` 低级接口

### `plotly` 字典接口
在较低的级别上，图可以表示为字典，并使用 `plotly.io` 模块中的函数显示。下图中的图字典描述了图。它包含轨迹和标题。

In [1]:
from plotly import graph_objects as go
go.FigureWidget(); # 初始化

In [2]:
import plotly.io as pio

fig = {
    'data': [
        {
            'type': 'bar',
            'x': [1, 2, 3],
            'y': [1, 3, 2]
        }
    ],
    'layout': {
        'title_text': 'Python 字典指定的图形'
    }
}
# 要显示该字典定义的图，请使用低级的 plot.io.show 函数
pio.show(fig)

### 图对象接口

[`plotly.graph_objects` 模块](https://plotly.com/python-api-reference/plotly.graph_objects.html) 提供了自动生成的称为 “[图对象（graph objects）](https://daobook.github.io/plotly-book/tutorial/fundamentals/34_graph-objects.html#plotly-graph-objects)” 的类层次结构，它有顶级类 `plotly.graph_objects.Figure` 可以用来表示图。

与普通的 Python 字典相比，图对象有几个优点。

1.  图对象提供精确的数据验证。如果提供无效的属性名或无效的属性值作为图形对象的键，将引发异常，并给出描述问题的有用错误消息。如果使用普通的 Python 字典和列表来构建图形，情况就不一样了。

2.  图对象以 Python 文档字符串的形式包含每个有效属性的描述，并提供[完整的 API 参考](https://plotly.com/python-api-reference/)。您可以在自己选择的开发环境中使用这些文档字符串来了解可用的属性，作为[在线参考](https://plotly.com/python/reference/index/)的替代方法。

3.  图对象的属性可以通过字典式的键查找（如`fig["layout"]`）或类式的属性访问（如`fig.layout`）来访问。

4.  图对象支持对已构造的图（`.update_layout()`，`.add_trace()`等）进行更新的高级便利函数，如下所述。

5.  图对象构造器和更新方法接受“魔法下划线”（例如 `go.Figure(layout_title_text="The Title"` 而不是`dict(layout=dict(title=dict(text="The Title")))`）以获得更紧凑的代码，如下所述。

6.  图对象支持附加渲染（`.show()`）和导出函数（`.write_image()`），这些函数自动地从 [`plotly.io` 模块](https://plotly.com/python-api-reference/plotly.io.html) 调用适当的函数。

使用图对象：

In [3]:
import plotly.graph_objects as go

fig = go.Figure(
    data=[go.Bar(x=[1, 2, 3],
                 y=[1, 3, 2]),
    go.Scatter(x=[1, 2, 3],
                 y=[1, 3, 2])],
    layout=go.Layout(
        title=go.layout.Title(text="Python 字典指定的图形")
    )
)

fig.show()

还可以直接通过将字典传递给 `go.Figure` 的构造函数来创建图对象。

In [4]:
import plotly.graph_objects as go

dict_of_fig = {
    'data': [
        {
            'type': 'bar',
            'x': [1, 2, 3],
            'y': [1, 3, 2]
        }
    ],
    'layout': {
        'title': {
            'text': 'Python 字典指定的图形'
        }
    }
}
fig = go.Figure(dict_of_fig)

fig.show()

### 将图对象转换为字典和 JSON

图对象可以使用 `fig.to_dict()` 方法转换为它们的 Python 字典表示形式。您也可以使用 `fig.to_json()` 方法检索图形对象的 JSON 字符串表示。

In [5]:
import plotly.graph_objects as go

fig = go.Figure(
    data=[go.Bar(x=[1, 2, 3], y=[1, 3, 2])],
    layout=go.Layout(height=600, width=800)
)

fig.layout.template = None  # to slim down the output

print(f"图对象的字典表示：\n{fig.to_dict()}\n\n")
print(f"图对象的 JSON 表示：\n{fig.to_json()}")

图对象的字典表示：
{'data': [{'x': [1, 2, 3], 'y': [1, 3, 2], 'type': 'bar'}], 'layout': {'height': 600, 'width': 800}}


图对象的 JSON 表示：
{"data":[{"x":[1,2,3],"y":[1,3,2],"type":"bar"}],"layout":{"height":600,"width":800}}


## 高级接口

### Plotly Express

[Plotly Express](https://daobook.github.io/plotly-book/tutorial/fundamentals/03_plotly-express.html#plotly-plotly-express)（来自 `plotly.express` 模块）是高级数据可视化 API，它可以在单个函数调用中生成完全填充的图对象。


In [6]:
import plotly.express as px

df = px.data.iris()
fig = px.scatter(df, x="sepal_width",
                 y="sepal_length", color="species", 
                 title="A Plotly Express Figure")
# 如果您打印图，您将看到它只是一个带有数据和布局的常规图
# print(fig)
fig.show()

### 图对象 `Figure` 构造器

如上所示，您可以通过将轨迹和布局规范传递给 `plotly.graph_objects.Figure` 构造函数来构建完整的图。这些轨迹和布局规范可以是字典或图对象。

在下面的示例中，使用图对象指定轨迹，并将布局指定为字典。

In [7]:
import plotly.graph_objects as go

fig = go.Figure(
    data=[go.Bar(x=[1, 2, 3], y=[1, 3, 2])],
    layout={'title': {'text': '由图形对象指定的图形'}}
)

fig.show()

### 图工厂

[Figure Factories](https://daobook.github.io/plotly-book/tutorial/fundamentals/32_figure-factories.html#plotly-figure-factories)（在 `plotly.py` 中的 `plotly.figure_factory` 模块中）是生成图对象的函数，通常是为了满足专门领域的需求。下面是使用 `create_quiver()` 图工厂构造一个图对象的示例，该图形显示 2D 箭头（quiver）图。

In [8]:
import numpy as np
import plotly.figure_factory as ff

x1,y1 = np.meshgrid(np.arange(0, 2, .2), np.arange(0, 2, .2))
u1 = np.cos(x1)*y1
v1 = np.sin(x1)*y1

fig = ff.create_quiver(x1, y1, u1, v1)
fig.show()

### 创建子图

`plotly.subplots.make_subplots()` 函数生成一个图对象，该图预先配置了一组可添加轨迹的子图网格。下面将进一步讨论 `add_trace()` 函数。


In [9]:
from plotly.subplots import make_subplots

fig = make_subplots(rows=1, cols=2)
fig.add_trace(go.Scatter(y=[4, 2, 1], mode="lines"),
              row=1, col=1)
fig.add_trace(go.Bar(y=[2, 1, 3]),
              row=1, col=2)

fig.show()